# Практикум 9

In [1]:
import pandas as pd
import seaborn as sns
import itertools as it
from collections import defaultdict
import re
import numpy as np
from sklearn.metrics import auc, f1_score #добавил второе для уверенности



import plotly.express as px # да-да, я ленивый
import plotly.graph_objects as go


import warnings
warnings.filterwarnings('ignore')

/home/bush29/anaconda3/lib/python3.9/site-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.24.2
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


In [2]:
with open('./lst_acc.txt', 'r') as file1:
    dom_ac_lst = [i.split(' ')[0] for i in file1.readlines()]
with open('full_seq.fasta', 'r') as file2:
    full_lst_acc = [i.split(' ')[0][1:] for i in file2.readlines() if i[0]==">"]
print(len(set(full_lst_acc).intersection(set(dom_ac_lst))))
bool_ac_lst = [(i in dom_ac_lst) for i in full_lst_acc]
ac_table = pd.DataFrame.from_dict({'AC':full_lst_acc,'Selected':bool_ac_lst} )

40


In [3]:
with open('full_seq.fasta', 'r') as file2:
    file_lst = file2.readlines()
grouper = it.groupby(file_lst,lambda x: x[0] == '>')
ac = None
my_seq = defaultdict(str)
for i,j in grouper:
    j = list(j)
    ac = j[0].split()[0][1:] if i else ac
    if not i and ac in dom_ac_lst:
        my_seq[ac] += ''.join(j)
with open('my_seq.fa', 'w') as file3:
    keys = list(my_seq.keys())
    values = list(my_seq.values())
    file3.writelines(f'>{keys[i]}\n{values[i]}' for i in range(len(my_seq)))

In [4]:
#манипуляции с output
lst_cols = ['E-value ' ,'score','bias','exp','N','Sequence','Description']
with open('temp_file.tsv', 'r') as file1:
    lst_strings = [re.sub(r' +', ',', i.strip()).split(',')[-7:] for i in file1.readlines()]
my_data = pd.DataFrame(lst_strings, columns=lst_cols)
my_data['With_domain'] = [i in dom_ac_lst for i in my_data.Sequence ]
my_data.drop(['Description',"bias",'exp','N'], inplace=True, axis=1)
my_data.loc[:,['E-value ','score']] = my_data.loc[:,['E-value ','score']].astype(float)
my_data.to_csv('output_data.csv', index=False) #забавно, что в не все посл-ти прошли порог по выравниванию(962 посл-ти в PFAM, содержащих выбранный домен)   
my_data

E-value   score          Sequence  With_domain
0    4.500000e-220  725.5      Q91UI9_9VIRU         True
1    6.000000e-215  708.6  A0A0A7MB71_9VIRU         True
2    1.700000e-214  707.0  A0A0A7M910_9VIRU         True
3    1.300000e-212  700.8      Q0VZC7_9VIRU         True
4    2.500000e-212  699.9  A0A0A7M8T8_9VIRU         True
..             ...    ...               ...          ...
102   1.200000e-10   32.3      F8VAG3_9VIRU        False
103   2.900000e-09   27.7  A0A1X9PY60_9VIRU        False
104   4.400000e-09   27.1      Q67701_9VIRU        False
105   2.500000e-08   24.6        CAPSD_SHVX        False
106   1.500000e-02    5.5  A0A1W5W6D7_9VIRU        False

[107 rows x 4 columns]

In [5]:
fig = px.histogram(my_data, x='score',nbins=35, title='The distribution of scores', color='With_domain', range_x=[750,0])
fig.show()

In [6]:
from dataclasses import dataclass

@dataclass
class My_model:
    thresh:float
    
    def predict(self, scores):
        self._last_pred = list(np.array(scores)>self.thresh)
        return self._last_pred
    
    def assess_me(self, y_true):
        y_pred = self._last_pred
        temp_table = np.array([y_true,y_pred])
        TP = np.sum(temp_table[1,:][temp_table[0,:]])
        P = np.sum(temp_table[0,:])
        TN = np.sum(~temp_table[1,:][~temp_table[0,:]])
        N = np.sum(~temp_table[0,:])
        pres = TP/(TP+N-TN)
        recall = TP/P
        spec = TN/N 
        return recall, spec, pres 

In [7]:
lst_one_minus_spec = []
lst_sens = []
lst_pres = []
lst_f1_score = []
scores = list(my_data.score.values)
lst_thresh = my_data.score.values
for thresh in lst_thresh:
    model = My_model(thresh=thresh)
    preds = model.predict(scores=scores)
    sens, spec, pres = model.assess_me(my_data.With_domain)
    lst_sens.append(sens)
    lst_one_minus_spec.append(1-spec)
    lst_pres.append(pres)
    lst_f1_score.append(f1_score(y_true = my_data.With_domain, y_pred=preds))  #1/((1/recall)+(1/pres))   

data_for_roc = pd.DataFrame({'1-specificity':lst_one_minus_spec, 'sensitivity':lst_sens, 'legend':len(lst_sens)*['model']})

fig = go.Figure()

fig.add_trace(go.Scatter(x=data_for_roc['1-specificity'], y=data_for_roc['sensitivity'], name='model',
                         line=dict(color='blue', width=4)))

fig.add_trace(go.Scatter(x=np.linspace(0,1,100), y=np.linspace(0,1,100),
                    mode='lines',
                    name='baseline', 
                    line=dict(color='red', width=4, dash='dash')))
fig.update_layout(title=f'ROC curve, AUC={ auc(np.sort(lst_one_minus_spec),np.array(lst_sens)[np.argsort(lst_one_minus_spec)])}',margin=dict(l=20, r=20, t=50, b=20), width=600, height=500, xaxis_range=[-0.02,1.02],yaxis_range=[-0.02,1.02], xaxis_title='1-specificity', yaxis_title='recall' )
fig.show()        

In [8]:
print(lst_thresh[np.argmax(np.array(lst_f1_score[:]))])  # какой-то баг в чьем-то сознании, пересчитывал и через sklearn, и своим кодом, результат был такой же

129.5


А можно посмотреть и по гистограмме, и понять,что хороший порог ~ 120

# Гистограмма длин белков семейства

In [9]:
fig = px.histogram( x=[len(i.replace('\n', '')) for i in my_seq.values()],nbins=30, title='The distribution of protein\'s lengths and their boxplot', marginal='box')
fig.show()

# таблица для отчета)

In [10]:
with open('my_align_post_rev.fa', 'r') as file1:
    selected_seq = [i[1:-7] for i in file1.readlines() if i.startswith('>') ]
my_data['HMM_selection'] = [i.Sequence in selected_seq for i in my_data.itertuples()]
my_data = my_data.loc[:,['Sequence', 'With_domain', 'HMM_selection', 'E-value ', 'score']]
my_data['1-specificity'] = lst_one_minus_spec
my_data['sensetivity'] = lst_sens
my_data['f1_score'] = lst_f1_score # Уверяю вас это правильно\
my_data

Sequence  With_domain  HMM_selection       E-value   score  \
0        Q91UI9_9VIRU         True           True  4.500000e-220  725.5   
1    A0A0A7MB71_9VIRU         True           True  6.000000e-215  708.6   
2    A0A0A7M910_9VIRU         True           True  1.700000e-214  707.0   
3        Q0VZC7_9VIRU         True           True  1.300000e-212  700.8   
4    A0A0A7M8T8_9VIRU         True           True  2.500000e-212  699.9   
..                ...          ...            ...            ...    ...   
102      F8VAG3_9VIRU        False          False   1.200000e-10   32.3   
103  A0A1X9PY60_9VIRU        False          False   2.900000e-09   27.7   
104      Q67701_9VIRU        False          False   4.400000e-09   27.1   
105        CAPSD_SHVX        False          False   2.500000e-08   24.6   
106  A0A1W5W6D7_9VIRU        False          False   1.500000e-02    5.5   

     1-specificity  sensetivity  f1_score  
0         0.000000        0.000  0.000000  
1         0.000000        0.025  0.048780  
2         0.000000        0.050  0.095238  
3         0.000000        0.075  0.139535  
4         0.000000        0.100  0.181818  
..             ...          ...       ...  
102       0.895522        1.000  0.571429  
103       0.940299        1.000  0.559441  
104       0.955224        1.000  0.555556  
105       0.970149        1.000  0.551724  
106       0.985075        1.000  0.547945  

[107 rows x 8 columns]

In [11]:
ac_table.to_csv('my_ac.csv', index=False)